In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [3]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)


  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)


  # Calculate Loss (for both TRAIN and EVAL modes)
  onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
  loss = tf.losses.softmax_cross_entropy(
      onehot_labels=onehot_labels, logits=logits)


  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)


  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [4]:

def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)

  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [5]:
if __name__ == "__main__":
  tf.app.run()

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001CF93275208>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:probabilities = [[ 0.09291986  0.11073665  0.10818701  0.10839596  0.090

INFO:tensorflow:loss = 2.30365, step = 1
INFO:tensorflow:probabilities = [[ 0.09784874  0.1126611   0.10062614  0.09858291  0.0898445   0.08622227
   0.09498887  0.0905698   0.11486964  0.11378593]
 [ 0.10114356  0.11007699  0.09482212  0.10524002  0.09606004  0.09960315
   0.08321229  0.09267613  0.1023023   0.11486332]
 [ 0.09693303  0.09876537  0.09300792  0.10795712  0.09963143  0.09638268
   0.0941961   0.10398893  0.09742877  0.11170867]
 [ 0.10511208  0.10305945  0.10142679  0.11577583  0.09282465  0.09399041
   0.08510318  0.09484614  0.10166927  0.10619224]
 [ 0.10420892  0.10116681  0.09606285  0.10781758  0.09940762  0.08520009
   0.09542938  0.10786831  0.09864259  0.10419585]
 [ 0.09715553  0.10418257  0.09051554  0.11159265  0.0969357   0.10324335
   0.09048931  0.09849188  0.09795897  0.10943455]
 [ 0.10902584  0.09785423  0.09471087  0.10517795  0.09822341  0.09511546
   0.09777422  0.10445236  0.09506346  0.10260215]
 [ 0.10104629  0.09582093  0.08892421  0.11022317  0

INFO:tensorflow:global_step/sec: 3.29623
INFO:tensorflow:probabilities = [[ 0.10355995  0.11111209  0.09921344  0.10535321  0.09508447  0.09391534
   0.08909008  0.08246591  0.11163832  0.10856727]
 [ 0.10474404  0.10177963  0.09512525  0.09185778  0.09986129  0.0897908
   0.101734    0.10480847  0.10347831  0.10682046]
 [ 0.1100544   0.10110008  0.09293857  0.11522651  0.11295488  0.09935467
   0.07951185  0.08687501  0.09828817  0.10369588]
 [ 0.09156807  0.10735426  0.09544962  0.10150727  0.10484906  0.10425555
   0.09117228  0.09867179  0.10021991  0.10495222]
 [ 0.10282861  0.10813105  0.09489664  0.10948513  0.09853436  0.10014445
   0.09041595  0.08345722  0.11120173  0.1009049 ]
 [ 0.09621861  0.1101261   0.10264677  0.10702317  0.1039127   0.09009198
   0.08727708  0.09510484  0.09563718  0.11196144]
 [ 0.10460372  0.10549439  0.09924179  0.1164864   0.09804495  0.0838406
   0.0891377   0.09705027  0.1056792   0.10042097]
 [ 0.10230286  0.09486096  0.09991233  0.10704248  0.1

INFO:tensorflow:loss = 2.28892, step = 101 (30.357 sec)
INFO:tensorflow:probabilities = [[ 0.09671605  0.11203129  0.09844244  0.10991939  0.09031586  0.09725156
   0.0872762   0.09058654  0.11537518  0.10208551]
 [ 0.09568106  0.11297268  0.10091054  0.10096257  0.09694677  0.09464212
   0.09133425  0.09674324  0.09582828  0.11397858]
 [ 0.09351668  0.10691275  0.10056883  0.09460367  0.10866087  0.08909247
   0.09826226  0.09582768  0.10276012  0.10979464]
 [ 0.10219891  0.09905268  0.10387762  0.10408551  0.09425764  0.09637118
   0.09424458  0.0974649   0.09877439  0.1096726 ]
 [ 0.10189293  0.094786    0.09019493  0.10108642  0.11402182  0.08749585
   0.08392769  0.09750666  0.10762953  0.12145828]
 [ 0.10714956  0.0959248   0.0975796   0.10493702  0.09735005  0.09569756
   0.08293899  0.09460411  0.10489254  0.11892579]
 [ 0.10172463  0.10433674  0.09495831  0.10581229  0.09507991  0.08996046
   0.09989464  0.10013557  0.09462602  0.11347142]
 [ 0.09544805  0.09636206  0.11362915

INFO:tensorflow:global_step/sec: 3.4
INFO:tensorflow:probabilities = [[ 0.09722172  0.10451353  0.09177011  0.11627363  0.09631061  0.09273215
   0.09299121  0.09870212  0.10038132  0.10910358]
 [ 0.09828585  0.10807281  0.09379496  0.10577992  0.10167494  0.09488785
   0.0893415   0.08889735  0.10569071  0.11357413]
 [ 0.10336993  0.09595624  0.10654324  0.1056378   0.12055787  0.09449272
   0.07803404  0.09487198  0.09824493  0.10229123]
 [ 0.09468263  0.11131959  0.10062905  0.1046401   0.09917998  0.09887237
   0.08406068  0.08955716  0.09480322  0.12225518]
 [ 0.10429161  0.09234131  0.0958308   0.09857777  0.11207722  0.09633643
   0.09679361  0.10140926  0.09511685  0.10722511]
 [ 0.08791122  0.10483622  0.09795378  0.09847062  0.10313644  0.10388774
   0.09789399  0.0944045   0.10256203  0.10894348]
 [ 0.09969657  0.10830782  0.09189493  0.10387835  0.09937771  0.09620401
   0.09192961  0.09720102  0.09804897  0.11346096]
 [ 0.09716492  0.09053349  0.1038141   0.12560788  0.099

...

INFO:tensorflow:global_step/sec: 3.31039
INFO:tensorflow:probabilities = [[ 0.00007813  0.01349598  0.00040618  0.00115303  0.00000888  0.00003865
   0.00000005  0.976004    0.00090999  0.00790508]
 [ 0.00006209  0.00919966  0.83207697  0.07776771  0.00180624  0.00262364
   0.07064339  0.0008603   0.00469272  0.0002673 ]
 [ 0.00001537  0.00000024  0.00274901  0.00251508  0.00002032  0.00101236
   0.00000009  0.00000061  0.95231354  0.04137342]
 [ 0.00000605  0.00000086  0.0021268   0.99114078  0.0000001   0.00001603
   0.          0.00000051  0.00666672  0.00004222]
 [ 0.00000842  0.00002932  0.00000236  0.00025281  0.00000006  0.99943417
   0.00000413  0.00000046  0.00025249  0.00001577]
 [ 0.00056022  0.00000711  0.0013575   0.00000746  0.00239716  0.00016448
   0.99519438  0.0000174   0.00028296  0.00001123]
 [ 0.00001529  0.          0.00000005  0.00001498  0.00000599  0.00004049
   0.          0.99884331  0.00000001  0.00107984]
 [ 0.01048904  0.00238839  0.01402727  0.00496049  0

INFO:tensorflow:loss = 0.110948, step = 19901 (30.200 sec)
INFO:tensorflow:probabilities = [[ 0.00003554  0.00000133  0.00016887  0.00000029  0.00130454  0.00010027
   0.99827099  0.00000002  0.00011798  0.00000024]
 [ 0.00000132  0.0000024   0.00003227  0.00025633  0.00013747  0.00007494
   0.          0.98988336  0.00024863  0.00936331]
 [ 0.00000001  0.          0.00000006  0.00000005  0.99956673  0.000001
   0.00000037  0.00000364  0.00000387  0.00042426]
 [ 0.00004161  0.00000039  0.00007264  0.00001287  0.05804666  0.00045388
   0.00006395  0.01831241  0.00076535  0.92223024]
 [ 0.99884498  0.00000071  0.00049622  0.00003218  0.          0.00062058
   0.0000011   0.00000014  0.00000001  0.00000413]
 [ 0.00000001  0.00000003  0.00000056  0.00003552  0.00000007  0.0000008
   0.          0.99986637  0.00000059  0.00009612]
 [ 0.00003459  0.000001    0.00005017  0.0000645   0.01495417  0.00008509
   0.00000019  0.06375828  0.00000885  0.92104316]
 [ 0.00142288  0.00046512  0.00342542

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.131659.
INFO:tensorflow:Starting evaluation at 2018-01-27-00:16:11
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-01-27-00:16:22
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9694, global_step = 20000, loss = 0.101396
{'accuracy': 0.96939999, 'loss': 0.10139619, 'global_step': 20000}


SystemExit: 

c:\program files\python364\lib\site-packages\IPython\core\interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
